In [85]:
import pandas as pd
import geopandas
import json
import shapely
import ast
import numpy as np
from shapely.geometry import shape, mapping
import chardet
import ftfy

In [84]:
!pip install ftfy

You should consider upgrading via the '/Users/darts/Desktop/karduni/phproto/pipeline/venv/bin/python -m pip install --upgrade pip' command.


In [63]:
df = pd.read_csv("rawData/Mekong3_Filtered_Translated_227.csv")

In [64]:
df = df[~df["place"].isna()].copy()

In [66]:
df.head(100)

Unnamed: 0  Unnamed: 0.1  index            id  \
0            0             0    824  1.320000e+18   
1            1             1    961  1.320000e+18   
2            2             2   1114  1.320000e+18   
3            3             3   1593  1.320000e+18   
4            4             4   1792  1.320000e+18   
..         ...           ...    ...           ...   
95          95            95  89750  1.320000e+18   
96          96            96  90182  1.320000e+18   
97          97            97  90537  1.320000e+18   
98          98            98  91044  1.320000e+18   
99          99            99  91151  1.320000e+18   

                                                 text  \
0                                         Sleep well    
1   The model has a headache and is sick and has a...   
2         cr⚽ infected with COVID soon‼ ️💝 yqahyzqst    
3   johnson amp johnson suspends trial of anti-cov...   
4   Foreigners are dazed and interested in COVID a...   
..                                                ...   
95                 nakakasakit binti maglakad hahaha    
96  afternoon turn great kohsamui thailand postcov...   
97  nottoc tamsrimaneedeng ¸μà¹ ‰ à¸¡à¸²à¸à¹à¸à¸ ™...   
98     ok lang mapagod kasi buka isa lang klase ðÿ˜œ    
99  covid quãªn máº ¥ t ðÿ˜… thá »© ä'äƒng kã thi ...   

                                                 user  \
0   {'id': 150197205, 'id_str': '150197205', 'name...   
1   {'id': 285549728, 'id_str': '285549728', 'name...   
2   {'id': 72417371, 'id_str': '72417371', 'name':...   
3   {'id': 1032257401313943552, 'id_str': '1032257...   
4   {'id': 996890280, 'id_str': '996890280', 'name...   
..                                                ...   
95  {'id': 4292800817, 'id_str': '4292800817', 'na...   
96  {'id': 120093200, 'id_str': '120093200', 'name...   
97  {'id': 108853937, 'id_str': '108853937', 'name...   
98  {'id': 147530481, 'id_str': '147530481', 'name...   
99  {'id': 92454361, 'id_str': '92454361', 'name':...   

                                                  geo  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3                                                 NaN   
4                                                 NaN   
..                                                ...   
95                                                NaN   
96                                                NaN   
97                                                NaN   
98                                                NaN   
99  {'type': 'Point', 'coordinates': [21.02892, 10...   

                                          coordinates  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3                                                 NaN   
4                                                 NaN   
..                                                ...   
95                                                NaN   
96                                                NaN   
97                                                NaN   
98                                                NaN   
99  {'type': 'Point', 'coordinates': [105.85463, 2...   

                                                place lang        time    yn  \
0   {'id': '00b250c861dafe8b', 'url': 'https://api...   th  10/14/2020  True   
1   {'id': '00b250c861dafe8b', 'url': 'https://api...   th  10/14/2020  True   
2   {'id': '00e3360a0d4c57c6', 'url': 'https://api...  und  10/14/2020  True   
3   {'id': '00f806f34e28b008', 'url': 'https://api...   th  10/14/2020  True   
4   {'id': '00609f9b3528fd98', 'url': 'https://api...   th  10/14/2020  True   
..                                                ...  ...         ...   ...   
95  {'id': '0198964b34b5128d', 'url': 'https://api...   tl  10/21/2

In [104]:
for i in df["text"]:
    print(ftfy.fix_text(i.encode("utf-8")))
    

UnicodeError: Hey wait, this isn't Unicode.

ftfy is designed to fix problems that were introduced by handling Unicode
incorrectly. It might be able to fix the bytes you just handed it, but the
fact that you just gave a pile of bytes to a function that fixes text means
that your code is *also* handling Unicode incorrectly.

ftfy takes Unicode text as input. You should take these bytes and decode
them from the encoding you think they are in. If you're not sure what encoding
they're in:

- First, try to find out. 'utf-8' is a good assumption.
- If the encoding is simply unknowable, try running your bytes through
  ftfy.guess_bytes. As the name implies, this may not always be accurate.

If you're confused by this, please read the Python Unicode HOWTO:

    http://docs.python.org/3/howto/unicode.html


In [16]:
df["place_dict"] = df.place.apply(ast.literal_eval)

In [17]:
df["centroid"] = df["place_dict"].apply(lambda x: shape(x["bounding_box"]).centroid)

In [18]:
df["centroid"]

0              POINT (100.5445395 13.78024)
1              POINT (100.5445395 13.78024)
2            POINT (100.4920285 13.7731125)
3               POINT (100.584323 13.78328)
4       POINT (99.94863300000002 14.019195)
                       ...                 
2423         POINT (106.6488975 11.1815385)
2424          POINT (100.4814615 13.781561)
2425    POINT (96.68302949999999 19.074708)
2426           POINT (104.840617 19.274218)
2427          POINT (105.655425 20.9746605)
Name: centroid, Length: 2427, dtype: object

In [19]:
geojson = geopandas.GeoSeries(df["centroid"]).__geo_interface__["features"]

In [20]:
df = df.replace(np.nan, '', regex=True)

In [21]:
df.columns

Index(['Unnamed: 0', 'Unnamed: 0.1', 'Unnamed: 0.1.1', 'index', 'id', 'text',
       'user', 'geo', 'coordinates', 'place', 'lang', 'time', 'yn',
       'matched strings', 'GESD', 'Prophet', 'clean_text', 'Anger', 'Disgust',
       'Fear', 'Joy', 'Sadness', 'Surprise', 'ents', 'locEnts', 'entity',
       'topic_id', 'place_dict', 'centroid'],
      dtype='object')

In [23]:
df_records = df.drop(["centroid","place_dict"],axis=1).to_dict('records')

In [24]:
for j, properties in zip(geojson,df_records):
    j["properties"] = properties
    j["properties"]["topic"] = properties["topic_id"]

In [25]:
with open("Mekong3_Filtered_Translated_227_processed.geojson","w") as jsonFile:
    jsonFile.write(json.dumps(geojson))

In [26]:
jsonstring = json.dumps(geojson)

In [27]:
jsonstring[2325:2340]

"e': False, 'fol"

In [31]:
from unidecode import unidecode

ModuleNotFoundError: No module named 'unidecode'

In [42]:
for i in geojson:
    print(i["properties"]["text"].encode('utf-32').decode("utf-32"))

Sleep well 
The model has a headache and is sick and has a fever 
cr⚽ infected with COVID soon‼ ️💝 yqahyzqst 
johnson amp johnson suspends trial of anti-covid vaccine after participants were found to be ill for unknown reasons 
Foreigners are dazed and interested in COVID and want to be interested in helping our home, but in the past a lot of media. But not moving in any way… mgoawpodk 
thailand report new covid case quarantin arriv india japan south sudan uae rais total
yzguaevv gotzyredlips​ thankyou love covid thank grate thank happi follow…  fjsptd 
Covid impact on the economy That affects the middle class grassroots Should cause overall motorcycle sales nationally… pvlnitpi 
th day of Vietnam is not covid new in the community of oumlrof 
Urgently, the masses clashed, injured people were reported. The number and symptoms still not yet known, King's talk, the second October mob news, click here… bibslirl 
Two injured mobs collided, hastening to separate the shore. chthailandnew Peop

Vietnamese infographs of the Vietnamese version of covid axzbscqzuq 
à¸žà¸'à¸à¸ ± à¸ "à¸ • à¸ ± à¸§à¹à¸-à¸ ™ à¸à¸ ± à¹à¸ ‡ à¸~à¸ ™ à¸" à¹à. ¸²à¹ƒà¸šà¹ ‰ à¸à¹à¸²à¸ ¢ à¸-à¸μà¹à¹ € à¸ £ à¸²à¸ "à¸§à¸šà¸" à¸¸à¸¡à¹ "à¸¡à¹à¹" à¸. "à¹ ‰ à¸ªà¸šà¸²à¸ ¢ à¹ƒà¸ à¸> à¸ £ à¸ ° à¸à¸ ± à¸ ™ à¸ªà¸¸à¸,à¸ à¸²à¸žà¹ € à. Covid â € ¦ xhkwihdrji 
zero confirm case covid todai chonburi pattaya banglamung week new case howeverâ€¦  bplmwoeh
project verita covid go dissappear
For now Kingpoweronlin shoppingonlin covid For now â € ¦ ybjijvgsng 
ramacovid ° iflshqdsb fmxqbsiydm 
hahaha if you are weak, die first, you will get covid 
hong kong base artist put dumpl mug taiwanes american artist creat ceram dumpl indian aâ€¦  padkjo
covid shit beam light lfc properli celebr leagu titl win byâ€¦  dpucxuer
Â € Â € ÂÂÂÂÂÂÂÂ € ÂÂÂ For the USA â € ¸¹à¹ ‰ â € <à¸ • à¸'à¸ "à¹ € à¸šà¸ · à¹ ‰ à¸â € <à¸à¸§à¹à¸²â € <à¸ ¥ à¹ ‰ à¸²à¸ ™. à¸ "à¸ ™ à¸ • à¹ ‰ à¸à¸ ™ à¸ £ à¸ ± â € <à¸šâ € <à¸> à¸ £ à¸ ° à¸~à¸²à¸ ™ à¸²à. Covid vtjydorr 

In [53]:
df = pd.read_csv("rawData/VietCam_Filtered_Translated_227.csv")

In [60]:
for d in df["text"]:
    print(d)

luiscarrillo vietnam day without contagion by covid how do you achieve pmrqqxb through the venezue radio network ... 
luiscarrillo vietnam day without contagion by covid how do you achieve pmrqqxb through the venezue radio network ... 
luiscarrillo vietnam day without contagion by covid how do you achieve pmrqqxb through the venezue radio network ... 
evernevertrump vietnam hasn gotten credit handl covid dens popul countri peopl andâ€¦
drzoehyd studi describ covid superspread event bar vietnam index case infect peopl contact wereâ€¦
bfriedmandc covid death new zealand vietnam south korea australia japan germani
bfriedmandc covid death new zealand vietnam south korea australia japan germani httâ€¦
bfriedmandc covid death new zealand vietnam south korea australia japan germani
bfriedmandc covid death new zealand vietnam south korea australia japan germani
bfriedmandc covid death new zealand vietnam south korea australia japan germani
bfriedmandc covid death new zealand vietnam south kore

emericanjohnson treatment test covid free vietnam  vutfbhggjm
can you not want to know how lao country brunei cambodia vietnam and thailand fight covid Ã ° Ã¿Ëœâ € � covid ssixyxpd 
emericanjohnson treatment test covid free vietnam
lordjordi lafabregat mireiapujol how can you explain that vietnam covid near china looks like tanÃ ¢ â‚¬Â¦ ucavhpx 
elfairi lordjordi lafabregat mireiapujol how can you explain that vietnam covid near china seems to close border 
vietnamÃ¢â‚¬â„¢ war covid Ã¢â‚¬â€œ theÃ¢ diplomat  ihomjqrq
new covid case octob china australia vietnamÃ¢â‚¬Â¦  seznuvyir
Ã¢â‚¬Å“the white hous recent new case covid new zealand taiwan vietnam combinedÃ¢â‚¬ï¿½
mireiapujol lordjordi lafabregat vietnam dead covid something we did bÃ £ Â © europe bmwsncjq 
I want Vietnam and my son, after the corona has collapsed 
hoan ngoc tanu green pseuderanthemumpalatiferum bloodpressur flu vietnam shop Ã ¢ â‚¬Â¦ pqwaimxlpq 
iuidfellowship idboardreview visit vietnam Ã°Ã¿â€¡Â»Ã°Ã¿â€¡Â³ amp wk post

birdyword have littl look vietnam arrest spread covid march thanÃ¢â‚¬Â¦
birdyword have littl look vietnam arrest spread covid march thanÃ¢â‚¬Â¦
insidervietnam foreign expert initi test posit covid depart vietnam retestsÃ¢ neg  yooekbÃ¢â‚¬Â¦
birdyword have littl look vietnam arrest spread covid march thanÃ¢â‚¬Â¦
pai taiwÃ £ Â¡n completed day in a row without local contagion covid all rÃ £ Â © cord vietnam has not detected infection for weeks 
Partaisocm Vietnam hurts first has fun then Indonesia has fun first has fun then Vietnam passes 
pai taiwÃ £ Â¡n completed day in a row without local contagion covid all rÃ £ Â © cord vietnam has not detected infection for weeks 
kirstieallei blame pari covid trump bout spain itali britain vietnam peru belgium mexico bolivia brazÃ¢â‚¬Â¦
pai taiwÃ £ Â¡n completed day in a row without local contagion covid all rÃ £ Â © cord vietnam has not detected infection for weeks 
birdyword have littl look vietnam arrest spread covid march thanÃ¢â‚¬Â¦
opinion vi

drzoehyd everydai life hanoi vietnam mask need zerocovid  ufxlvkaf
drzoehyd peopl wonder achiev vietnam lot effort elimin covid point earÃ¢â‚¬Â¦
drzoehyd peopl wonder achiev vietnam lot effort elimin covid point earÃ¢â‚¬Â¦
drzoehyd everydai life hanoi vietnam mask need zerocovid  ufxlvkaf
drzoehyd everydai life hanoi vietnam mask need zerocovid  ufxlvkaf
drzoehyd peopl wonder achiev vietnam lot effort elimin covid point earÃ¢â‚¬Â¦
drzoehyd peopl wonder achiev vietnam lot effort elimin covid point earÃ¢â‚¬Â¦
drzoehyd everydai life hanoi vietnam mask need zerocovid  ufxlvkaf
drzoehyd peopl wonder achiev vietnam lot effort elimin covid point earÃ¢â‚¬Â¦
drzoehyd everydai life hanoi vietnam mask need zerocovid  ufxlvkaf
drzoehyd peopl wonder achiev vietnam lot effort elimin covid point earÃ¢â‚¬Â¦
drzoehyd everydai life hanoi vietnam mask need zerocovid  ufxlvkaf
drzoehyd everydai life hanoi vietnam mask need zerocovid  ufxlvkaf
drzoehyd peopl wonder achiev vietnam lot effort elimin covid po

alberta fact lost peopl covid week vietnam oveÃ¢â‚¬Â¦  jiyknwzi
registryreport itÃ¢â‚¬â„¢ malaria med vietnam Ã°Ã¿â€¡Â»Ã°Ã¿â€¡Â³ Ã°Ã¿Ëœâ‚¬
npr new report covid death total time number kill year vietnam conflict mÃ¢â‚¬Â¦  tcfafwexsw
contrast asean economi vietnam succeed keep covid control rise export haveÃ¢â‚¬Â¦  dgpkzgrqxx
nikkeiasia contrast asean economi vietnam succeed keep covid control rise export heÃ¢â‚¬Â¦
nikkeiasia contrast asean economi vietnam succeed keep covid control rise export heÃ¢â‚¬Â¦
fud janicedean realdonaldtrump vietnam veteran upstat new york nurs home covid neg Ã¢â‚¬Â¦  qtjoagynpm
mfathai kudo vietnam job execut asean chair covid year thumb choic suchÃ¢â‚¬Â¦
stopherbuck speakerpelosi trump covid kill count equal approxim vietnam war herman cain
mfathai kudo vietnam job execut asean chair covid year thumb choic suchÃ¢â‚¬Â¦
jojocucaracha alberta fact lost peopl covid week vietnam theÃ¢â‚¬Â¦
hughacheson digitjon thereÃ¢â‚¬â„¢ virtual covid australia new zealand sout

...

drzoehyd prepar christma hanoi vietnam Ã°Ã¿Å¾â€¦Ã°Ã¿Å¾â€ž countri gone dai record local case covid theÃ¢â‚¬Â¦
coronaviru yoga beer cambodia breweri help peopl reliev covid stress januari  nÃ¢â‚¬Â¦  tbclrea
orla hegarti Ã°Ã¿â€¡Â»Ã°Ã¿â€¡Â³ vietnam covid airlin precaut dzunglevn covidisairborn
drzoehyd prepar christma hanoi vietnam Ã°Ã¿Å¾â€¦Ã°Ã¿Å¾â€ž countri gone dai record local case covid theÃ¢â‚¬Â¦
orla hegarti Ã°Ã¿â€¡Â»Ã°Ã¿â€¡Â³ vietnam covid airlin precaut dzunglevn covidisairborn  gozbbtllp
vietnam record new covid case total asian countri gone consecut dai withoutÃ¢â‚¬Â¦  ffbtxt
vietnam record new covid case total asian countri gone consecut dai new covÃ¢â‚¬Â¦
vietnam bigger popul death covid total
vanessavu schadet der kampf gegen covid der wirtschaft fall von vietnam bedeutet zerocovid da gegenteil schloss da landÃ¢â‚¬Â¦
lasillarota vietnam una poblaciÃ£Â³n millon hai sÃ£Â³lo persona muerta por covid lopezobrador Ã¢â‚¬Â¦  zqmxzgxjb
iskonglasalista vietnam complet studi pilot prog

kkmputrajaya new zealand vietnam dan taiwan tersenarai sebagai negara negara terbaik menguru pandemik covid malaysia mendudukiÃ¢â‚¬Â¦
covid plu nouveaux ca vietnam le premier deux moi  acwyncpzi rfi covid vietnam
mariaressa new zealand vietnam taiwan rank success fight covid  bqpnbtc
ajamubaraka socialist republ vietnam covid death dispar socialist orient nation amp capiÃ¢â‚¬Â¦
gh vietnam prais success control covid face fresh wave infect todai Ã°Ã¿â€¡Â»Ã°Ã¿â€¡Â³ reportedÃ¢â‚¬Â¦
aldosteron vietnam mort covid tout le pai qui Ã£Â©coutent leur mÃ£Â©decin sÃ¢â‚¬â„¢en sortent mieux que ceux qui Ã£Â©coutent big pÃ¢â‚¬Â¦
abcnew saw new sai vietnam taiwan best handl covid outbreak
ajamubaraka socialist republ vietnam covid death dispar socialist orient nation amp capiÃ¢â‚¬Â¦
ajamubaraka socialist republ vietnam covid death dispar socialist orient nation amp capiÃ¢â‚¬Â¦
aldosteron vietnam mort covid tout le pai qui Ã£Â©coutent leur mÃ£Â©decin sÃ¢â‚¬â„¢en sortent mieux que ceux qui Ã£Â©coutent b

cirogomezl iztapalapa tien mÃ£Â¡ muerto por covid que australia dinamarca vietnam alcaldÃ£Â­a reporta mil fallecido poÃ¢â‚¬Â¦
cirogomezl iztapalapa tien mÃ£Â¡ muerto por covid que australia dinamarca vietnam alcaldÃ£Â­a reporta mil fallecido poÃ¢â‚¬Â¦
cirogomezl iztapalapa tien mÃ£Â¡ muerto por covid que australia dinamarca vietnam alcaldÃ£Â­a reporta mil fallecido poÃ¢â‚¬Â¦
cirogomezl iztapalapa tien mÃ£Â¡ muerto por covid que australia dinamarca vietnam alcaldÃ£Â­a reporta mil fallecido poÃ¢â‚¬Â¦
cirogomezl iztapalapa tien mÃ£Â¡ muerto por covid que australia dinamarca vietnam alcaldÃ£Â­a reporta mil fallecido poÃ¢â‚¬Â¦
cirogomezl iztapalapa tien mÃ£Â¡ muerto por covid que australia dinamarca vietnam alcaldÃ£Â­a reporta mil fallecido poÃ¢â‚¬Â¦
cirogomezl iztapalapa tien mÃ£Â¡ muerto por covid que australia dinamarca vietnam alcaldÃ£Â­a reporta mil fallecido poÃ¢â‚¬Â¦
cirogomezl iztapalapa tien mÃ£Â¡ muerto por covid que australia dinamarca vietnam alcaldÃ£Â­a reporta mil fallecido po

lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames 

lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
updat covid vietnam  dpnkbjqgv
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
lunaoi vietnam face new wave covid strain vietnames afraid quarantin frÃ¢â‚¬Â¦
tricor group releas asia pacif trade report focus impact rcep vietnam covid recoveri  cjonqxei
lunao

In [54]:
import csv

In [55]:
with open("rawData/Mekong3_Filtered_Translated_227.csv") as csvFile:
    csvReader = csv.DictReader(csvFile)
    data = [row for row in csvReader]

In [56]:
for d in data:
    print(d["text"].encode().decode())

Sleep well 
The model has a headache and is sick and has a fever 
cr⚽ infected with COVID soon‼ ️💝 yqahyzqst 
johnson amp johnson suspends trial of anti-covid vaccine after participants were found to be ill for unknown reasons 
Foreigners are dazed and interested in COVID and want to be interested in helping our home, but in the past a lot of media. But not moving in any way… mgoawpodk 
thailand report new covid case quarantin arriv india japan south sudan uae rais total
yzguaevv gotzyredlips​ thankyou love covid thank grate thank happi follow…  fjsptd 
Covid impact on the economy That affects the middle class grassroots Should cause overall motorcycle sales nationally… pvlnitpi 
th day of Vietnam is not covid new in the community of oumlrof 
Urgently, the masses clashed, injured people were reported. The number and symptoms still not yet known, King's talk, the second October mob news, click here… bibslirl 
Two injured mobs collided, hastening to separate the shore. chthailandnew Peop

à¸ ‰ à¸ ± à¸ ™ à¹ "à¸¡à¹à¸à¸ ¥ à¹ ‰ à¸²à¸à¸à¸à¸à¸²à¸à¸šà¹ ‰ à¸²à¸ ™ à¹" à. ¸> à¸-à¸³à¸ ‡ à¸²à¸ ™ à¸ ‰ à¸ ± à¸ ™ à¸à¸ ¥ à¸ ± à¸§à¸§à¸§ à¸šà¹à¸§à¸ ¢. à¸ "à¹ ‰ à¸§à¸ ¢ à¸ ¢ à¸ ¢ à¸ ¢ à¸ ¢ à¸ ¢ à¸ ¢ à¸ ¢ à¹,à¸" à¸§à¸'à¸ "covid à¸œà. ¸ à¹ "à¸¡à¹à¸ªà¸ ± à¹à¸ ‡ à¸> à¸'à¸" ðÿ~. 
ã,¿ ã ¤ ã ¯ç · šæ € ¥ æ³ • ä »¤ç¬¬å. ¨ã.—ã € æœˆæ— ¥ ã.®å.ˆå ‰.æ ™ ã.‹ ç � † ã ™ ã ‹ã ÿã � ¸ »ã ª ç ¹ã ¯ã € �å ›½ã ¨ã. — »¤ã € �ã ل¬ã ¹ã يˆã ل © ã ل³ã. �å � è ‡ ª æ² »ä½" 
troubl panic ahead covid varieti mr goo forget phone wentâ€¦  skocqv
covid ˆ ˆ à¸-à¸ªà¸²à¸~à¸²à¸ £ à¸ "à¸ ° à¸ £ à¸-à¸ªà¹à¸§à¸ ™ à¸ • à¸ ± à¸§à¹" à¸¡à¹à. ¸ • à¸ £ à¸§à¸ à¹ € à¸> à¹ ‡ à¸ ™ à¸ ¢ à¸ ± à¸ ‡ à¹ "à¸ ‡ à¸ ¥ à¸ ° à¹" à¸> à¹,à¸. œà¸ ¥ à¹à¸ à¸¹à¸-à¸ ± à¸šà¹ € à¸šà¸'à¸à¸à¸μà¸à¹à¸ ¥ à¹ ‰ à¸§ à¹,à¸ "à¸§. next 
richardbarrow covid list air pollut road accid
awai covid à¸šà¸à¸ £ à¸¸à¸ ‡ à¹ € à¸-à¸žà¸¯à¹à¸ ¥ à¹ ‰ à¸§ à¹à¸ "à¸ ‡ à¹ € à¸-à¸ ·. yqqfncee 
à¸à¸ £ à¸¸à¸ "à¸ªà¸§à¸ ± à¸ªà¸" à¸'à¹œà¸§à¸ ± à¸ ™ à¸à¸ ± à¸ ™ à¸à¸ £. Next ... You are here: jcfcx